In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 5GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/halite/kaggle-environments.zip


Neural Network Agent version nn_call.py

In [2]:
from kaggle_environments.envs.halite.helpers import *

import torch

device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

torch.set_default_tensor_type('torch.FloatTensor')


# NN params
in_channels = 10
middle_channels = 32
policy_channels = 5
value_channels = 1
# middle_layer_count = 1
random_seed = None

# training params
lr = 0.0001
betas = (0.9, 0.999)
gamma = 0.99
# eps_clip = 0.2
alpha_value = 0.8
alpha_entropy = 0

# global variables
my_player_id = 0
player_halite = 0
enemy_halite = 0
current_step = 0
terminal_state = False
eliminated = False
episode_tracking = 0

max_episodes = 100
max_timesteps = 400
update_timestep = 30
min_update_steps = 5
save_interval = 10

# diagnostic stuff
save_replay = False
num_replays = 3
print_probs = False
print_loss = False

max_ships = 20
ship_count = 0


# submission stuff
square_probs = False
eval_setting = False


##################################################################################
##################################################################################
##################################################################################
##################################################################################



import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F

from torch.distributions import Categorical

import datetime
import random


class InputBlock(nn.Module):
    def __init__(self):
        super(InputBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 10, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock1(nn.Module):
    def __init__(self):
        super(DenseBlock1, self).__init__()
        self.conv = nn.Conv2d(in_channels = 26, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):

        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock2(nn.Module):
    def __init__(self):
        super(DenseBlock2, self).__init__()
        self.conv = nn.Conv2d(in_channels = 42, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class DenseBlock3(nn.Module):
    def __init__(self):
        super(DenseBlock3, self).__init__()
        self.conv = nn.Conv2d(in_channels = 58, out_channels = 16, kernel_size = 3, stride = 1)
        self.bn = nn.BatchNorm2d(16)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return F.relu(self.bn(self.conv(state)))

class PolicyBlock(nn.Module):
    def __init__(self):
        super(PolicyBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 74, out_channels = 5, kernel_size = 3, stride = 1)
        self.logsoftmax = nn.LogSoftmax(dim = 1)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        return self.logsoftmax(self.conv(state)).exp()


class ValueBlock(nn.Module):
    def __init__(self):
        super(ValueBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels = 74, out_channels = 1, kernel_size = 3, stride = 1)

    def forward(self, state):
        state = F.pad(state, (1, 1, 1, 1), 'circular')
        state = F.relu(self.conv(state))
        return state

class ActorCritic(nn.Module):
    def __init__(self):
        super(ActorCritic, self).__init__()

        self.input_conv = InputBlock().to(device)

        self.dense1 = DenseBlock1().to(device)
        self.dense2 = DenseBlock2().to(device)
        self.dense3 = DenseBlock3().to(device)

        self.policy_out = PolicyBlock().to(device)
        self.value_out = ValueBlock().to(device)

    def forward(self):
        raise NotImplementedError

    def get_action_output(self, state):
        temp1 = self.input_conv(state)
        temp1 = torch.cat((state, temp1), dim = 1)

        temp2 = self.dense1(temp1)
        temp2 = torch.cat((temp1, temp2), dim = 1)

        temp3 = self.dense2(temp2)
        temp3 = torch.cat((temp2, temp3), dim = 1)

        temp4 = self.dense3(temp3)
        temp4 = torch.cat((temp3, temp4), dim = 1)

        action_map = self.policy_out(temp4)

        return action_map

    def get_actions(self, state, ship_dict, memory):
        action_map = self.get_action_output(state)
        batch_size = state.size()[0]
        action_dict = {}

        new_ship_locs = state[0][1].detach().clone()
        for ship_id in ship_dict.keys():
            # ship action vector represented by first 6 layers of action output
            ship_loc = ship_dict[ship_id][0]
            ship_loc = (ship_loc // 21, ship_loc % 21)
            if ship_id in memory.states.keys():
                memory.states[ship_id].append(state)
                memory.locations[ship_id].append(ship_loc)
            else:
                memory.states[ship_id] = [state]
                memory.locations[ship_id] = [ship_loc]


            actionprobs = torch.stack((action_map[0][0][ship_loc[0]][ship_loc[1]],
                                       action_map[0][1][ship_loc[0]][ship_loc[1]],
                                       action_map[0][2][ship_loc[0]][ship_loc[1]],
                                       action_map[0][3][ship_loc[0]][ship_loc[1]],
                                       action_map[0][4][ship_loc[0]][ship_loc[1]]))

            if print_probs == True:
                print(actionprobs)
            if square_probs == True:
                actionprobs = torch.mul(actionprobs, actionprobs)

            # action masking
            mask = [1, 1, 1, 1, 1]
            # north
            if new_ship_locs[(ship_loc[0]-1)%21, ship_loc[1]] == 1:
                mask[0] = 0
            # east
            if new_ship_locs[ship_loc[0], (ship_loc[1]+1)%21] == 1:
                mask[1] = 0
            # south
            if new_ship_locs[(ship_loc[0]+1)%21, ship_loc[1]] == 1:
                mask[2] = 0
            # west
            if new_ship_locs[ship_loc[0], (ship_loc[1]-1)%21] == 1:
                mask[3] = 0
            # wait logic
            if mask[0] + mask[1] + mask[2] + mask[3] == 0:
                mask[4] = 1
            elif state[0][3][ship_loc] == 1:
                mask[4] = 0

            actionprobs = torch.mul(actionprobs, torch.tensor(mask).to(device))

            dist = Categorical(actionprobs)
            action = dist.sample()

            action_dict[ship_id] = action
            if ship_id in memory.actions.keys():
                memory.actions[ship_id].append(action)
                memory.logprobs[ship_id].append(dist.log_prob(action))
                memory.conflict_maps[ship_id].append(new_ship_locs.detach().clone())
            else:
                memory.actions[ship_id] = [action]
                memory.logprobs[ship_id] = [dist.log_prob(action)]
                memory.conflict_maps[ship_id] = [new_ship_locs.detach().clone()]

            # update ship loc
            # north
            if action == 0:
                new_ship_locs[(ship_loc[0]-1)%21, ship_loc[1]] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # east
            elif action == 1:
                new_ship_locs[ship_loc[0], (ship_loc[1]+1)%21] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # south
            elif action == 2:
                new_ship_locs[(ship_loc[0]+1)%21, ship_loc[1]] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0
            # west
            elif action == 3:
                new_ship_locs[ship_loc[0], (ship_loc[1]-1)%21] = 1
                new_ship_locs[ship_loc[0], ship_loc[1]] = 0

        return action_dict, new_ship_locs

    def get_logprobs_entropies(self, key, memory):
        # occurs during update, ship_dict should only be a single ship
        logprobs = []
        entropies = []
        for idx in range(len(memory.states[key])):
            state = memory.states[key][idx]
            action_map = self.get_action_output(state)
            ship_loc = memory.locations[key][idx]
            conflict_map = memory.conflict_maps[key][idx]

            actionprobs = torch.stack((action_map[0][0][ship_loc[0]][ship_loc[1]],
                                       action_map[0][1][ship_loc[0]][ship_loc[1]],
                                       action_map[0][2][ship_loc[0]][ship_loc[1]],
                                       action_map[0][3][ship_loc[0]][ship_loc[1]],
                                       action_map[0][4][ship_loc[0]][ship_loc[1]]))

            # action masking
            mask = [1, 1, 1, 1, 1]
            # north
            if conflict_map[(ship_loc[0]-1)%21, ship_loc[1]] == 1:
                mask[0] = 0
            # east
            if conflict_map[ship_loc[0], (ship_loc[1]+1)%21] == 1:
                mask[1] = 0
            # south
            if conflict_map[(ship_loc[0]+1)%21, ship_loc[1]] == 1:
                mask[2] = 0
            # west
            if conflict_map[ship_loc[0], (ship_loc[1]-1)%21] == 1:
                mask[3] = 0
            # wait logic
            if mask[0] + mask[1] + mask[2] + mask[3] == 0:
                mask[4] = 1
            elif state[0][3][ship_loc] == 1:
                mask[4] = 0

            actionprobs = torch.mul(actionprobs, torch.tensor(mask).to(device))

            dist = Categorical(actionprobs)

            logprobs.append(dist.log_prob(memory.actions[key][idx]))
            entropies.append(dist.entropy())


        logprobs = torch.stack(logprobs).to(device)
        entropies = torch.stack(entropies).to(device)

        return logprobs, entropies

    def get_value_map(self, state):
        temp1 = self.input_conv(state)
        temp1 = torch.cat((state, temp1), dim = 1)

        temp2 = self.dense1(temp1)
        temp2 = torch.cat((temp1, temp2), dim = 1)

        temp3 = self.dense2(temp2)
        temp3 = torch.cat((temp2, temp3), dim = 1)

        temp4 = self.dense3(temp3)
        temp4 = torch.cat((temp3, temp4), dim = 1)

        value_map = self.value_out(temp4)

        return value_map[0][0]



##################################################################################
##################################################################################
##################################################################################
##################################################################################



import torch

import datetime

def process_state(state):
    current_player = state.player

    halite_plane = np.reshape(np.array(state.halite), (21, 21))

    ally_ship_plane = np.zeros([441])
    ally_cargo_plane = np.zeros([441])
    ally_yard_plane = np.zeros([441])
    enemy_ship_plane = np.zeros([441])
    enemy_cargo_plane = np.zeros([441])
    enemy_yard_plane = np.zeros([441])
    empty_plane = np.full([441], 1)

    for player_id in range(len(state.players)):
        if player_id == current_player:
            # state.observation.players[player_id][2] is the dictionary of ships with key being ship ID
            # and value being [location, cargo amount]
            for ship in state.players[player_id][2].keys():
                ally_ship_plane[state.players[player_id][2][ship][0]] = 1
                ally_cargo_plane[state.players[player_id][2][ship][0]] = state.players[player_id][2][ship][1]
                empty_plane[state.players[player_id][2][ship][0]] = 0
            for yard in state.players[player_id][1].keys():
                ally_yard_plane[state.players[player_id][1][yard]] = 1
                empty_plane[state.players[player_id][1][yard]] = 0
        else:
            for ship in state.players[player_id][2].keys():
                enemy_ship_plane[state.players[player_id][2][ship][0]] = 1
                enemy_cargo_plane[state.players[player_id][2][ship][0]] = state.players[player_id][2][ship][1]
                empty_plane[state.players[player_id][2][ship][0]] = 0
            for yard in state.players[player_id][1].keys():
                enemy_yard_plane[state.players[player_id][1][yard]] = 1
                empty_plane[state.players[player_id][1][yard]] = 0

    ally_ship_plane = np.reshape(ally_ship_plane, (21, 21))
    ally_cargo_plane = np.reshape(ally_cargo_plane, (21, 21))
    ally_yard_plane = np.reshape(ally_yard_plane, (21, 21))
    enemy_ship_plane = np.reshape(enemy_ship_plane, (21, 21))
    enemy_cargo_plane = np.reshape(enemy_cargo_plane, (21, 21))
    enemy_yard_plane = np.reshape(enemy_yard_plane, (21, 21))
    empty_plane = np.reshape(empty_plane, (21, 21))


    halite_plane = np.divide(halite_plane, 500)
    ally_cargo_plane = np.divide(ally_cargo_plane, 500)
    enemy_cargo_plane = np.divide(enemy_cargo_plane, 500)

    player_halite_plane = np.full([441], player_halite)
    player_halite_plane = np.reshape(player_halite_plane, (21, 21))
    player_halite_plane = np.divide(player_halite_plane, 500)

    timestep_plane = np.full([441], current_step)
    timestep_plane = np.reshape(timestep_plane, (21, 21))
    timestep_plane = np.divide(timestep_plane, 400)

    output = np.stack((halite_plane, ally_ship_plane, ally_cargo_plane, ally_yard_plane,
                     enemy_ship_plane, enemy_cargo_plane, enemy_yard_plane, empty_plane,
                     player_halite_plane, timestep_plane))

    return torch.unsqueeze(torch.tensor(output).float().to(device), 0)




##################################################################################
##################################################################################
##################################################################################
##################################################################################

import base64

model_string = b'...'


decoded_model = base64.b64decode(model_string)


##################################################################################
##################################################################################
##################################################################################
##################################################################################


import numpy as np

import torch
import torch.nn as nn
from io import BytesIO


class Memory:
    def __init__(self):
        self.actions = {}
        self.locations = {}
        self.next_locations = {}
        self.logprobs = {}
        self.rewards = {}
        self.states = {}
        self.next_states = {}
        self.conflict_maps = {}

    def clear(self):
        self.actions = {}
        self.locations = {}
        self.next_locations = {}
        self.logprobs = {}
        self.rewards = {}
        self.states = {}
        self.next_states = {}
        self.conflict_maps = {}

class PPO:
    def __init__(self):
        # hyperparams defined in config.py
        self.lr = lr
        self.betas = betas
        self.gamma = gamma


        self.policy = ActorCritic()
        if eval_setting == True:
            self.policy.eval()
        self.policy.float()
        self.policy.to(device)

        self.policy.load_state_dict(torch.load(BytesIO(decoded_model)))

        self.optimizer = torch.optim.Adam(self.policy.parameters(), lr = self.lr, betas = self.betas)





##################################################################################
##################################################################################
##################################################################################
##################################################################################





import torch
import torch.nn as nn

import numpy as np

from kaggle_environments import make






ppo = PPO()
memory = Memory()

def NN_call(obs, config, ship_dict):
	state = obs
	if isinstance(state, list):
		state = state[0]

	my_player_id = state.player

	submit_dict = {}

	ship_action_translate = {0: 'NORTH', 1: 'EAST', 2: 'SOUTH', 3: 'WEST', 4: 'WAIT'}

	player_halite = state.players[my_player_id][0]

	state_grid = process_state(state)

	action_dict, new_ship_locs = ppo.policy.get_actions(state_grid, ship_dict, memory)


	for key in ship_dict.keys():
        	if action_dict[key].item() != 4:
        		submit_dict[key] = ship_action_translate[action_dict[key].item()]


	memory.clear()

	return submit_dict


Hard coded agent version aug25.py

In [3]:
%%writefile submission.py

from kaggle_environments.envs.halite.helpers import *

# Directions a ship can move
directions = [ShipAction.NORTH, ShipAction.EAST, ShipAction.SOUTH, ShipAction.WEST]

# Will keep track of whether a ship is collecting halite or carrying cargo to a shipyard
ship_states = {}

chase_counter = {}
#should make list for each ship with last moves, if last move was none for more than X turns, randmoize.

# Returns the commands we send to our ships and shipyards
def agent(obs, config):
    size = config.size
    board = Board(obs, config)
    me = board.current_player
    
    ################################
    # Imports and helper functions #
    ################################   

    import random

    # Takes a tuple with both values between (-size+1) to (size-1) and returns a vector with both values between -size/2 to size/2 by modding with size
    def vectorMod(x,y):
        if x<-size/2: 
            x= x+size
        if x>size/2: 
            x=x-size
        if y<-size/2: 
            y=y+size
        if y>size/2: 
            y=y-size
        return (x,y)

    # Returns best (not unique) direction to move from one position (fromPos) to another (toPos)
    # Example: If I'm at pos (0,0) and want to get to pos (0,20), I should choose South direction
    def getDirTo(fromPos, toPos):
        a= toPos[0]-fromPos[0]
        b= toPos[1]-fromPos[1]
        c=vectorMod(a,b)    
        ret1 = ShipAction.EAST
        ret2 = ShipAction.NORTH
        if c[0]>0: ret1 = ShipAction.EAST
        if c[0]<0: ret1 = ShipAction.WEST
        if c[1]>0: ret2 = ShipAction.NORTH
        if c[1]<0: ret2 = ShipAction.SOUTH
        if c[0]==0: return ret2
        if c[1]==0: return ret1
        if random.randint(0, 1)==0: return ret1  
        else: return ret2
        
        
    #doesn't consider optimal path positions now, e.g. (0,0) to (2,3): is it better to move north or east every step?

    #Returns distance between two positions
    def distFromTo(fromPos, toPos):
        a= toPos[0]-fromPos[0]
        b= toPos[1]-fromPos[1]
        c=vectorMod(a,b)
        return abs(c[0])+abs(c[1])

    #Returns a cell containing the maximum halite in a 2*radius+1 box around ship
    def maxHalitePos(ship,radius):
        x = ship.cell.position.x
        y = ship.cell.position.y
        max = ship.cell.halite
        ret = board[x,y]
        for i in range(x-radius,x+radius):
            for j in range(y-radius,y+radius):
                c=vectorMod(i,j)
                s=c[0]
                t=c[1]
                if c[0]<0: 
                    s=c[0]+size
                if c[1]<0: 
                    t=c[1]+size                    
                C = board[s,t]
                if max <= C.halite:
                    ret = C
                    max = C.halite
        return ret
    

    #Returns the closest ally shipyard to ship
    def closestAllyShipyard(ship):
        if len(me.shipyards)==0:
            return None
        ret=me.shipyards[0]
        minn=distFromTo(ship.position,ret.position)
        for shipyard in me.shipyards:
            dist=distFromTo(ship.position,shipyard.position)
            if dist<minn:
                minn=dist
                ret=shipyard
        return ret
    
    #Finds the closest ally ship to shipyard
    def closestAllyShip(shipyard):
        if len(me.ships)==0:
            return None
        ret=me.ships[0]
        minn=distFromTo(shipyard.position,ret.position)
        for ship in me.ships:
            dist=distFromTo(shipyard.position,ship.position)
            if dist<minn:
                minn=dist
                ret=ship
        return ret

    #Finds the closest ally collector ship to shipyard
    def closestcollectorShip(shipss,shipyard):
        if len(shipss)==0:
            return None
        ret=shipss[0]
        minn=distFromTo(shipyard.position,ret.position)
        for ship in shipss:
            dist=distFromTo(shipyard.position,ship.position)
            if dist<minn:
                minn=dist
                ret=ship
        return ret

    #Returns the closest enemy ship to ship
    def closestEnemyShip(ship):
        enemy_ships = [ship for ship in board.ships.values() if ship not in me.ships]
        if len(enemy_ships)==0:
            return None
        ret=enemy_ships[0]
        minn=distFromTo(ship.position,ret.position)
        for enemy_ship in enemy_ships:
            dist=distFromTo(ship.position,enemy_ship.position)
            if dist<minn:
                minn=dist
                ret=enemy_ship
        return ret

    #Returns the closest enemy ship to a shipyard
    def closestEnemyShiptoShipyard(shipyard):
        enemy_ships = [ship for ship in board.ships.values() if ship not in me.ships]
        if len(enemy_ships)==0:
            return None
        ret=enemy_ships[0]
        minn=distFromTo(shipyard.position,ret.position)
        for enemy_ship in enemy_ships:
            dist=distFromTo(shipyard.position,enemy_ship.position)
            if dist<minn:
                minn=dist
                ret=enemy_ship
        return ret

    #Returns the closest enemy shipyard to ship
    def closestEnemyShipyard(ship):
        enemy_shipyards = [shipyard for shipyard in board.shipyards.values() if shipyard not in me.shipyards]
        if len(enemy_shipyards)==0:
            return None
        ret=enemy_shipyards[0]
        minn=distFromTo(ship.position,ret.position)
        for enemy_shipyard in enemy_shipyards:
            dist=distFromTo(ship.position,enemy_shipyard.position)
            if dist<minn:
                minn=dist
                ret=enemy_shipyard
        return ret
    
    #Returns the opposite direction to direction
    def oppositeDir(direction):
        if direction:
            return directions[(directions.index(direction)+2)%4]

    #Finds the enemy with one rank away from you in terms of halite (priorotizing Higher rank)
    def closestEnemyHalite(player): #player: Player -> Player
    
        players_halite = {p : p.halite for p in board.opponents}
        if len(players_halite)==1:
            return player
        if len(players_halite)==0:
            return None
        players_halite = sorted(players_halite.items(), key=lambda x: x[1], reverse=True)
        player_index = players_halite.index((player,player.halite))
        if player_index==0:
            return players_halite[1][0]
        else:
            return players_halite[player_index-1][0]

    #Finds ship with low halite for one player (typically player is s me)
    def shipsslowhalite(shipss):
        lowhalitecounter=75
        return [s for s in shipss if s.halite<lowhalitecounter]
    
    #Finds ship with lowest halite not in above definition, or highest halite in above definition if former doesn't exist
    def shipsslowesthalite(play):
        if play.ships==[]:
            return None
        if len(play.ships)>0:
            abovelowhaliteships=[s for s in play.ships if s not in shipsslowhalite(play.ships)]
            if abovelowhaliteships==[]:
                shipcan=shipsslowhalite(play.ships)[0]
                for ss in shipcan:
                    if ss.halite>shipcan.halite:
                        ss=shipcan
                return shipcan
            if len(abovelowhaliteships)>0:
                shipcan=abovelowhaliteships[0]
                for s in abovelowhaliteships:
                    if s.halite<shipcan.halite:
                        s=shipcan
                return shipcan
    
    #11111find the closest enemy shipyard one rank above you relative to ships with low halite
    def closestenemyShipyardrelship(shipss):
        if shipss==None:
            return None
        ene1=opponentHalite(me)
        if ene1==None:
            return None
        if len(ene1.shipyards)==0:
            return None
        ene=ene1.shipyards[0]
        if shipsslowhalite(shipss)==[]:
            return None
        my=shipsslowhalite(shipss)[0]
        for x in opponentHalite(me).shipyards:
            for y in shipss:
                if distFromTo(ene.position,my.position) > distFromTo(x.position,y.position):
                    ene=x
                    my=y
        tup=(ene,my)
        return tup

        
    # Returns best direction in order to collect
    def collect(ship):
        # If halite at current location running low, 
        # move to the adjacent square containing the most halite
        
        minHaliteToFarm = 100
        if ship.cell.halite < minHaliteToFarm:
            neighbors = [ship.cell.north.halite, ship.cell.east.halite, 
                         ship.cell.south.halite, ship.cell.west.halite]
            best = max(range(len(neighbors)), key=neighbors.__getitem__)
            return directions[best]

    # Returns best direction in order to collect

    #### need to upgrade so that if ships last move was the opposite of current move it changes (prevent loop where ships goes back and forth) ####

    def newCollect(ship):
        # If halite at current location running low, 
        # move to the adjacent square containing the most halite
        
        radius = 4
        minHaliteToFarm = 150

        if ship.cell.halite < minHaliteToFarm:
            C = maxHalitePos(ship,radius)
            direction = getDirTo(ship.position, C.position)
           # if direction: 
                #if direction == directions[(directions.index(ship.next_action)+2)%4]:
                  #  return ship.next_action
               # else: 
                 #   return direction
            if direction: 
                return direction

    #Returns best direction in order to deposit cargo 
    def deposit(ship):
        # Move towards shipyard to deposit cargo
        if closestAllyShipyard(ship) == None:
            return None
        direction = getDirTo(ship.position,closestAllyShipyard(ship).position)
        if direction: 
            return direction
        
    def shouldShipConvert(ship):
        if len(me.shipyards) == 0:
            return False
        shipyardMinDist = 7
        maxShipyards = 3
        convertCostMultiplier = 5
        if distFromTo(ship.position,closestAllyShipyard(ship).position)>shipyardMinDist and (ship.halite+me.halite)>convertCostMultiplier*config.convertCost and len(me.shipyards)<maxShipyards:
            return True
        return False
    
#     def shouldShipyardSpawn(shipyard):
#         spawnCostMultiplier = 3
#         stepInterval = 10
#         shipsPerShipyard = 4
#         maxRoundToSpawn = 300
#         if me.halite>spawnCostMultiplier*config.spawnCost and board.step%stepInterval == 0 and len(me.ships)<shipsPerShipyard*len(me.shipyards) and board.step<maxRoundToSpawn:
#             return True
#         return False
    
    def shouldShipyardSpawn(shipyard):
        minHaliteToSpawn = 1000
        maxShips = 25
        maxRoundToSpawn = 270
        if me.halite>minHaliteToSpawn and len(me.ships)<maxShips and board.step<maxRoundToSpawn:
            return True
        return False
    
    #AGENT
    
    
    
    cur_ships = me.ships # list that holds all ships that are not converting next action
    cur_shipyards = me.shipyards # list that holds all shipyards that are not spawning next action
    protector = []
    ship_role = {}
    
    if len(me.shipyards)>0:
        if board.step>=2:
            for ship in me.ships:
                if ship.position==me.shipyards[0].position:
                    chase_counter[ship.id] = 0   
    
        
        
    #Early Game
    
    collectorcount=10 #one more than the number of collectors

    if board.step>=1 and board.step<=collectorcount:
        cur_shipyards[0].next_action = ShipyardAction.SPAWN
        cur_shipyards.pop(0)     
        
    # If there are no ships, use first shipyard to spawn a ship.
    if len(me.ships) == 0 and len(me.shipyards) > 0 and board.step>collectorcount:
        cur_shipyards[0].next_action = ShipyardAction.SPAWN
        cur_shipyards.pop(0)

    # If there are no shipyards, convert first ship into shipyard.
    if len(me.shipyards) == 0 and len(me.ships) > 0:
        cur_ships[0].next_action = ShipAction.CONVERT
        cur_ships.pop(0)
    
    #Splitting all ships into collecting and attacking groups, and designating one to protect
    
    
    if len(me.shipyards)>0 and len(cur_ships)>0:
        for ship in cur_ships:
            #collecting_ships = [shipId for shipId in ship_states.keys() if ship_states[shipId]=="COLLECT"]
            ship_distShipyard = [ (ship, distFromTo(ship.position,me.shipyards[0].position) ) for ship in cur_ships] 
            ship_distShipyard.sort(key = lambda x: x[1])  
            collectorshipno=min(len(cur_ships)-1,collectorcount)
            ship_role[ship_distShipyard[0][0]]="PROTECT"
            protector.append(ship_distShipyard[0][0])
            for i in range(1,collectorshipno+1):
                ship_role[ship_distShipyard[i][0]]="COLLECT"
    
    
    #Converting ships to shipyards
        
#     for ship in cur_ships:
        #if ship.next_action == None: 
            
#         if shouldShipConvert(ship):
#             ship.next_action = ShipAction.CONVERT
#             cur_ships.remove(ship)
#             continue  

        ### Part 1: Set the ship's state 
    
    minHaliteToDeposit = 500

    for ship in cur_ships:

                
        #11111Attacks enemy shipyards on purpose (does not depend on distance from them)
                
#             if closestenemyShipyardrelship(me.ships)!= None:
#                 if ship == closestenemyShipyardrelship(me.ships)[1]:
#                     shipyardkamikaze = closestenemyShipyardrelship(me.ships)[0]
#                     direction = getDirTo(ship.position, shipyardkamikaze.position)
#                     ship.next_action = direction

        if ship.halite <= minHaliteToDeposit: # If cargo is too low, collect halite
            ship.next_action = newCollect(ship)


        if ship.halite > minHaliteToDeposit: # If cargo gets very big, deposit halite
            ship.next_action = deposit(ship)

            #Calling NN agent for a deposit/collect scenario
    
#             ship_dict = {}
#             ship_dict[ship.id] = [ship.position.to_index(size),ship.halite]
#             action_ret=NN_call(obs, config, ship_dict)
#             directions_str=['NORTH', 'EAST', 'SOUTH', 'WEST']
#             if len(action_ret)==0:
#                 ship.next_action = None
#             else:
#                 ship.next_action = directions[directions_str.index(action_ret[ship.id])]             


    #Spawning Ships
                
    for shipyard in cur_shipyards:       
        if shouldShipyardSpawn(shipyard):
            shipyard.next_action = ShipyardAction.SPAWN
            cur_shipyards.remove(shipyard)
            
                   
    #Randomization
    
    if random.randint(0, 8)==0:
        for ship in cur_ships:
            ship.next_action = directions[random.randint(0,3)]
            
            
    # Make sure that non COLLECT ships actually follow other strong oponnents instead of newCollect()
    
    
    #Code
    
        
        #Making sure collecting ships are staying within the grid (note that only works with one shipyard)
#     if len(me.shipyards)>0 and len(me.ships)>0:
#         gridRadius = 5
        
#         ships_futurePos = []
#         for ship in cur_ships:      
#             if ship in ship_role.keys():          
#                 if ship.next_action==None:               
#                      ships_futurePos.append(ship.position)
#                 else:
#                      ships_futurePos.append(ship.position.translate(ship.next_action.to_point(), size))

#         for i in range(len(ships_futurePos)):
#             if abs(me.shipyards[0].position.x-ships_futurePos[i].x)>gridRadius or abs(me.shipyards[0].position.y-ships_futurePos[i].y)>gridRadius:
#                 cur_ships[i].next_action=oppositeDir(cur_ships[i].next_action)
        
            
    #Collision prevention or chase other player ships or shipyards
    
    enemyCollisionRadius = 2 # maybe 3?]
    enemyShipyardCollisionRadius = 4
    maxCargoToAllowDestroyingShipyard = 100
    
    for ship in me.ships: #using me.ships here because you want to stop CONVERT if it's worth to chase and to run away instead of CONVERTing if another ship is close
        #advanced: maybe you can still convert and then defend shipyard with by spawning a ship
        enemyShipyard = closestEnemyShipyard(ship)
        if enemyShipyard != None:
            if distFromTo(ship.position,enemyShipyard.position)<=enemyShipyardCollisionRadius and ship.halite < maxCargoToAllowDestroyingShipyard:
                direction=getDirTo(ship.position,enemyShipyard.position)
                if chase_counter[ship.id]>=0:
                    ship.next_action = direction
                chase_counter[ship.id]+=1
                if chase_counter[ship.id]==4:
                    chase_counter[ship.id]=-2
                    ship.next_action = oppositeDir(direction) 
                if chase_counter[ship.id]<0:
                    ship.next_action = oppositeDir(direction) 
        enemy = closestEnemyShip(ship)
        if enemy != None:
            if distFromTo(ship.position,enemy.position)<=enemyCollisionRadius:
                direction = getDirTo(ship.position,enemy.position)
                if ship.halite < enemy.halite:
                    if chase_counter[ship.id]>=0:
                        ship.next_action = direction
                    chase_counter[ship.id]+=1
                    if chase_counter[ship.id]==4:
                        chase_counter[ship.id]=-2
                        ship.next_action = oppositeDir(direction)  
                    if chase_counter[ship.id]<0:
                        ship.next_action = oppositeDir(direction) 
                else:
                    ship.next_action = oppositeDir(direction)        
            
    #Shipyard spawn collision check
    
    shipyard_collision = [] # list containing all next action position for ships in cur_ships
    for ship in cur_ships:
            if ship.next_action==None:               
                shipyard_collision.append(ship.position)
            else:
                shipyard_collision.append(ship.position.translate(ship.next_action.to_point(), size))
    shipyard_pos = [shipyard.position for shipyard in me.shipyards if shipyard not in cur_shipyards] # list containing all shipyards spawning ships in next action
    for shipyardPos in shipyard_pos:
        for i in range(len(shipyard_collision)):
            ship=cur_ships[i]
            if shipyardPos==shipyard_collision[i]:
                if ship.next_action==None:
                    ship.next_action = directions[random.randint(0,3)]
                else:
                    ship.next_action=oppositeDir(ship.next_action) 
                    
    #defender ship
    if len(me.shipyards)>0 and len(me.ships)>0:     
        defendRadius = 2
        for ship in protector:
            if ship.next_action!= None:
                coord=ship.position.translate(ship.next_action.to_point(), size)
            else:
                coord=ship.position
            if abs(me.shipyards[0].position.x-coord.x)>defendRadius or abs(me.shipyards[0].position.y-coord.y)>defendRadius:
                ship.next_action=oppositeDir(ship.next_action) #makes sure is in defending radius, need to code collection within radius
            enemy_ships = [ship for ship in board.ships.values() if ship not in me.ships]
            if len(enemy_ships)!=0:
                threat=closestEnemyShiptoShipyard(me.shipyards[0])
                if distFromTo(threat.position,me.shipyards[0].position)<=defendRadius+1:
                    if ship.position==me.shipyards[0].position:
                        me.shipyards[0].next_action = None
                        ship.next_action = None

                    else:
                        direction=getDirTo(ship.position,me.shipyards[0].position)
                        ship.next_action=direction
    
    #Collision prevention with self only
    #board_cpy=board.next()
    
    i=0
    while(True):
        collision_test = []
        for ship in cur_ships:
            if ship.next_action==None:               
                collision_test.append(ship.position)
            else:
                collision_test.append(ship.position.translate(ship.next_action.to_point(), size))
        duplicates = [index for index, pos in enumerate(collision_test) if pos in (collision_test[:index] + collision_test[(index+1):])]
        if len(duplicates)==0 or i==100:
            break
        for index in duplicates:
            ship=cur_ships[index]
            if ship.next_action != None:
                if ship not in protector:
                    if i<10:
                        ship.next_action = oppositeDir(ship.next_action)
                    else:
                        ship.next_action = directions[(directions.index(ship.next_action)+1+2*(i%2))%4]
        i+=1
    
    
    if board.step<=collectorcount:
        for ship in cur_ships:
            if ship.next_action == None:               
                collision_test=ship.position
            else:
                collision_test=ship.position.translate(ship.next_action.to_point(), size)
            if collision_test==me.shipyards[0].position:
                if ship.next_action != None:
                    ship.next_action = None
                else:
                    ship.next_action = directions[random.randint(0,3)]
           
    # Convert to shipyard if in last round ship has larger than 500 cargo    
            
    if board.step==398:
        for ship in me.ships:
            if ship.halite>500:
                ship.next_action = ShipAction.CONVERT
    
    
    #Prevent ships from crashing early game
    
                                       
    return me.next_actions


Writing submission.py


In [4]:
from kaggle_environments import make
env = make("halite", debug=True)
env.run(["submission.py", "submission.py", "submission.py", "submission.py"])
env.render(mode="ipython", width=800, height=600)